In [5]:
import warnings
warnings.filterwarnings('ignore')

# --- Library Imports ---
import pandas as pd
import numpy as np
import gc
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.cluster import KMeans
import lightgbm as lgb
import xgboost as xgb
import optuna

print("--- BLOCK 1: SETUP & IMPORTS ---")
print("Libraries imported successfully.")

# --- Haversine Distance Function ---
def haversine(lat1, lon1, lat2, lon2):
    R = 6371  # Earth radius in kilometers
    dLat = np.radians(lat2 - lat1)
    dLon = np.radians(lon2 - lon1)
    lat1 = np.radians(lat1)
    lat2 = np.radians(lat2)
    a = np.sin(dLat/2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dLon/2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    return R * c

# --- Global Constants ---
N_SPLITS = 5
RANDOM_STATE = 42
DATA_PATH = './'
N_OPTUNA_TRIALS = 30 
COMPETITION_ALPHA = 0.1

# --- Load Raw Data ---
try:
    df_train = pd.read_csv(DATA_PATH + 'dataset.csv', index_col="id", parse_dates=["sale_date"])
    df_test = pd.read_csv(DATA_PATH + 'test.csv', index_col="id", parse_dates=["sale_date"])
    print("Raw data loaded successfully.")
except FileNotFoundError:
    print("ERROR: Could not find 'dataset.csv' or 'test.csv'.")
    exit()

# --- Prepare Target Variable ---
y_log = np.log1p(df_train['sale_price'])
y_true = df_train['sale_price'].copy()
df_train['sale_price_log'] = y_log
df_train.drop('sale_price', axis=1, inplace=True)

print("Setup complete.")
print("-" * 50)


--- BLOCK 1: SETUP & IMPORTS ---
Libraries imported successfully.
Raw data loaded successfully.
Setup complete.
--------------------------------------------------


In [6]:
print("--- BLOCK 2: GOD-TIER FEATURE ENGINEERING ---")

# Combine for consistent processing
df_train['is_train'] = 1
df_test['is_train'] = 0
all_data = pd.concat([df_train, df_test], axis=0)

# Foundational Features
all_data['sale_year'] = all_data['sale_date'].dt.year
all_data['sale_month'] = all_data['sale_date'].dt.month
all_data['age_at_sale'] = all_data['sale_year'] - all_data['year_built']
all_data['total_bathrooms'] = all_data['bath_full'] + 0.5 * all_data['bath_half'] + 0.75 * all_data['bath_3qtr']
all_data['total_sqft'] = all_data['sqft'] + all_data['sqft_fbsmt']
all_data['was_renovated'] = (all_data['year_reno'] > 0).astype(int)
all_data['time_since_reno'] = np.where(all_data['was_renovated'] == 1, all_data['sale_year'] - all_data['year_reno'], all_data['age_at_sale'])
all_data['sin_sale_month'] = np.sin(2 * np.pi * all_data['sale_month']/12)
all_data['cos_sale_month'] = np.cos(2 * np.pi * all_data['sale_month']/12)

# Location and Distance Features
kmeans = KMeans(n_clusters=30, random_state=RANDOM_STATE, n_init='auto')
all_data['location_cluster'] = kmeans.fit_predict(all_data[['latitude', 'longitude']])
seattle_center_lat, seattle_center_lon = 47.6062, -122.3321
all_data['dist_to_center'] = haversine(all_data['latitude'], all_data['longitude'], seattle_center_lat, seattle_center_lon)

# Peer-Comparison & Target-Encoded Features
print("Creating peer-comparison features...")
train_copy_for_aggs = all_data[all_data['is_train'] == 1].copy()
group_cols_to_agg = ['location_cluster', 'city', 'submarket']

for group_col in group_cols_to_agg:
    aggs = {'grade': ['mean', 'std'], 'age_at_sale': ['mean', 'std'], 'total_sqft': ['mean', 'std'], 'sale_price_log': ['mean']}
    group_aggs = train_copy_for_aggs.groupby(group_col).agg(aggs)
    group_aggs.columns = [f'{c[0]}_{c[1]}_{group_col}' for c in group_aggs.columns]
    all_data = all_data.merge(group_aggs, on=group_col, how='left')
    all_data[f'grade_vs_mean_{group_col}'] = all_data['grade'] - all_data[f'grade_mean_{group_col}']
    all_data[f'sqft_vs_mean_{group_col}'] = all_data['total_sqft'] - all_data[f'total_sqft_mean_{group_col}']

# Final Cleanup
cols_to_drop = ['sale_date', 'year_built', 'year_reno', 'bath_full', 'bath_half', 'bath_3qtr', 'sqft', 'sqft_fbsmt', 'latitude', 'longitude', 'sale_price_log']
all_data = all_data.drop(columns=cols_to_drop)
for col in all_data.select_dtypes(include='object').columns:
    all_data[col] = pd.Categorical(all_data[col]).codes
all_data.fillna(0, inplace=True)
print("Feature engineering complete.")
print("-" * 50)


--- BLOCK 2: GOD-TIER FEATURE ENGINEERING ---
Creating peer-comparison features...
Feature engineering complete.
--------------------------------------------------


In [7]:
print("--- BLOCK 3: SMART FEATURE SELECTION ---")
temp_X = all_data[all_data['is_train'] == 1].drop(columns=['is_train'])
fs_model = lgb.LGBMRegressor(random_state=RANDOM_STATE, n_jobs=-1)
fs_model.fit(temp_X, y_log)
importances = pd.DataFrame({'feature': temp_X.columns, 'importance': fs_model.feature_importances_}).sort_values('importance', ascending=False)
useless_features = importances[importances['importance'] == 0]['feature'].tolist()
all_data.drop(columns=useless_features, inplace=True)
print(f"Dropped {len(useless_features)} useless features. Proceeding with {all_data.shape[1]-1} features.")
print("\nTop 20 most important features:")
display(importances.head(20))
del temp_X, fs_model, importances
gc.collect()
print("-" * 50)

--- BLOCK 3: SMART FEATURE SELECTION ---
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.021306 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5252
[LightGBM] [Info] Number of data points in the train set: 200000, number of used features: 73
[LightGBM] [Info] Start training from score 13.078327
Dropped 9 useless features. Proceeding with 64 features.

Top 20 most important features:


feature  importance
35                             sale_year         497
9                               land_val         280
10                               imp_val         254
2                            join_status         136
11                              sqft_lot         127
45                        dist_to_center         118
1                           sale_warning         110
4                                   area         107
37                           age_at_sale         105
41                       time_since_reno          93
39                            total_sqft          86
3                              join_year          85
13                                 grade          57
52  sale_price_log_mean_location_cluster          56
53        grade_vs_mean_location_cluster          54
12                                sqft_1          52
6                                 zoning          49
62                    grade_vs_mean_city          47
36                            sale_month          40
0                               sale_nbr          37

--------------------------------------------------


In [8]:
print("--- BLOCK 4: FINAL MODELING PIPELINE ---")
# Separate final datasets
X = all_data[all_data['is_train'] == 1].drop(columns=['is_train'])
X_test = all_data[all_data['is_train'] == 0].drop(columns=['is_train'])
X_test = X_test[X.columns]
grade_for_stratify = df_train['grade']

# Define Helper Functions
def winkler_score(y_true, lower, upper, alpha=0.1, return_coverage=False):
    width = upper - lower
    penalty_lower = np.where(y_true < lower, (2 / alpha) * (lower - y_true), 0)
    penalty_upper = np.where(y_true > upper, (2 / alpha) * (y_true - upper), 0)
    score = width + penalty_lower + penalty_upper
    if return_coverage:
        coverage = np.mean((y_true >= lower) & (y_true <= upper))
        return np.mean(score), coverage
    return np.mean(score)

def train_model_pipeline(model_type, X_train, y_train, X_test):
    print(f"\n--- Starting Pipeline for: {model_type.upper()} ---")
    
    # 1. Hyperparameter Tuning with Optuna
    def objective(trial):
        train_x, val_x, train_y, val_y = train_test_split(X_train, y_train, test_size=0.2, random_state=RANDOM_STATE)
        
        if model_type == 'lgbm':
            params = {
                'objective': 'quantile', 'metric': 'quantile', 'random_state': RANDOM_STATE, 'n_jobs': -1,
                'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1, log=True),
                'num_leaves': trial.suggest_int('num_leaves', 20, 150),
                'max_depth': trial.suggest_int('max_depth', 5, 12),
            }
            model_class = lgb.LGBMRegressor
            fit_params = {'callbacks': [lgb.early_stopping(50, verbose=False)]}
        else: # xgb
            params = {
                'objective': 'reg:quantileerror', 'eval_metric': 'rmse', 'tree_method': 'hist', 'random_state': RANDOM_STATE, 'n_jobs': -1,
                'eta': trial.suggest_float('eta', 0.01, 0.1, log=True),
                'max_depth': trial.suggest_int('max_depth', 4, 10),
                'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
            }
            model_class = xgb.XGBRegressor
            fit_params = {'early_stopping_rounds': 50, 'verbose': False} # This will fail on your old XGB, so we will use the functional API below

        preds_lower, preds_upper = np.zeros(len(val_y)), np.zeros(len(val_y))
        for i, alpha in enumerate([0.05, 0.95]):
            if model_type == 'lgbm':
                model = model_class(**params, n_estimators=1000, alpha=alpha)
                model.fit(train_x, train_y, eval_set=[(val_x, val_y)], **fit_params)
            else: # Use functional API for XGB
                dtrain = xgb.DMatrix(train_x, label=train_y)
                dval = xgb.DMatrix(val_x, label=val_y)
                xgb_params = {**params, 'quantile_alpha': alpha}
                model = xgb.train(xgb_params, dtrain, num_boost_round=1000, evals=[(dval, 'eval')], early_stopping_rounds=50, verbose_eval=False)
            
            preds = model.predict(val_x if model_type=='lgbm' else dval)
            if i == 0: preds_lower = preds
            else: preds_upper = preds
        
        return winkler_score(np.expm1(val_y), np.expm1(preds_lower), np.expm1(preds_upper), alpha=0.1)

    print(f"--- Tuning {model_type.upper()} ---")
    study = optuna.create_study(direction='minimize')
    study.optimize(objective, n_trials=N_OPTUNA_TRIALS, n_jobs=1)
    best_params = study.best_params
    
    # 2. K-Fold Training with Best Parameters
    print(f"--- K-Fold Training {model_type.upper()} with Best Params ---")
    skf = StratifiedKFold(n_splits=N_SPLITS, shuffle=True, random_state=RANDOM_STATE)
    oof_preds = np.zeros((len(X_train), 2))
    test_preds = np.zeros((len(X_test), 2))
    
    for fold, (train_idx, val_idx) in enumerate(skf.split(X_train, grade_for_stratify)):
        print(f"  Fold {fold+1}/{N_SPLITS}...")
        X_train_fold, y_train_fold = X_train.iloc[train_idx], y_train.iloc[train_idx]
        X_val_fold = X_train.iloc[val_idx]
        
        for i, alpha in enumerate([0.05, 0.95]):
            if model_type == 'lgbm':
                model = lgb.LGBMRegressor(**best_params, n_estimators=2000, objective='quantile', metric='quantile', random_state=RANDOM_STATE, n_jobs=-1, alpha=alpha)
                model.fit(X_train_fold, y_train_fold, eval_set=[(X_val_fold, y_train.iloc[val_idx])], callbacks=[lgb.early_stopping(100, verbose=False)])
                oof_preds[val_idx, i] = model.predict(X_val_fold)
                test_preds[:, i] += model.predict(X_test) / N_SPLITS
            else: # Use functional API for XGB
                dtrain = xgb.DMatrix(X_train_fold, label=y_train_fold)
                dval = xgb.DMatrix(X_val_fold, label=y_train.iloc[val_idx])
                dtest = xgb.DMatrix(X_test)
                xgb_params = {'objective': 'reg:quantileerror', 'eval_metric': 'rmse', 'tree_method': 'hist', 'random_state': RANDOM_STATE, 'n_jobs': -1, **best_params, 'quantile_alpha': alpha}
                model = xgb.train(xgb_params, dtrain, num_boost_round=2000, evals=[(dval, 'eval')], early_stopping_rounds=100, verbose_eval=False)
                oof_preds[val_idx, i] = model.predict(dval, iteration_range=(0, model.best_iteration))
                test_preds[:, i] += model.predict(dtest, iteration_range=(0, model.best_iteration)) / N_SPLITS
    
    return oof_preds, test_preds

# --- Run Pipelines for Both Models ---
oof_lgbm, test_lgbm = train_model_pipeline('lgbm', X, y_log, X_test)
oof_xgb, test_xgb = train_model_pipeline('xgb', X, y_log, X_test)

[I 2025-07-03 19:48:17,217] A new study created in memory with name: no-name-b57b737e-3630-41fd-9e98-83835cd91a1d


--- BLOCK 4: FINAL MODELING PIPELINE ---

--- Starting Pipeline for: LGBM ---
--- Tuning LGBM ---
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.006533 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5178
[LightGBM] [Info] Number of data points in the train set: 160000, number of used features: 64
[LightGBM] [Info] Start training from score 12.128117
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2025-07-03 19:59:58,401] A new study created in memory with name: no-name-b8245c58-1b3d-4dd7-aa55-84cc5332473d



--- Starting Pipeline for: XGB ---
--- Tuning XGB ---


[I 2025-07-03 20:00:36,669] Trial 0 finished with value: 350253.9233683594 and parameters: {'eta': 0.026136131061803073, 'max_depth': 8, 'min_child_weight': 8}. Best is trial 0 with value: 350253.9233683594.
[I 2025-07-03 20:01:13,409] Trial 1 finished with value: 344179.9023876953 and parameters: {'eta': 0.024475906436786637, 'max_depth': 7, 'min_child_weight': 7}. Best is trial 1 with value: 344179.9023876953.
[I 2025-07-03 20:02:03,339] Trial 2 finished with value: 355269.77054414066 and parameters: {'eta': 0.014934729423104053, 'max_depth': 8, 'min_child_weight': 4}. Best is trial 1 with value: 344179.9023876953.
[I 2025-07-03 20:02:37,009] Trial 3 finished with value: 346554.84049707034 and parameters: {'eta': 0.02995566938864341, 'max_depth': 5, 'min_child_weight': 1}. Best is trial 1 with value: 344179.9023876953.
[I 2025-07-03 20:03:18,401] Trial 4 finished with value: 343241.9896578125 and parameters: {'eta': 0.04988367847927773, 'max_depth': 7, 'min_child_weight': 6}. Best is

--- K-Fold Training XGB with Best Params ---
  Fold 1/5...
  Fold 2/5...
  Fold 3/5...
  Fold 4/5...
  Fold 5/5...


In [9]:
# --- Ensemble, Calibrate, and Submit ---
print("\n--- Final Ensembling and Calibration ---")
oof_ensemble = (oof_lgbm + oof_xgb) / 2
test_ensemble = (test_lgbm + test_xgb) / 2
oof_lower = np.expm1(oof_ensemble[:, 0])
oof_upper = np.expm1(oof_ensemble[:, 1])
oof_upper = np.maximum(oof_lower, oof_upper)
score, coverage = winkler_score(y_true, oof_lower, oof_upper, alpha=COMPETITION_ALPHA, return_coverage=True)
print(f"Final ENSEMBLE OOF Score (before calib): {score:,.2f} | Coverage: {coverage:.2%}")

best_factor = 1.0
best_coverage_diff = abs(coverage - 0.90)
for factor in np.arange(0.9, 1.2, 0.001):
    center = (oof_lower + oof_upper) / 2
    width = oof_upper - oof_lower
    _, current_coverage = winkler_score(y_true, center - (width / 2) * factor, center + (width / 2) * factor, alpha=COMPETITION_ALPHA, return_coverage=True)
    if abs(current_coverage - 0.90) < best_coverage_diff:
        best_coverage_diff = abs(current_coverage - 0.90)
        best_factor = factor
print(f"Best calibration factor found: {best_factor:.3f}")

test_lower = np.expm1(test_ensemble[:, 0])
test_upper = np.expm1(test_ensemble[:, 1])
test_center = (test_lower + test_upper) / 2
test_width = test_upper - test_lower
calibrated_lower = test_center - (test_width / 2) * best_factor
calibrated_upper = test_center + (test_width / 2) * best_factor
calibrated_upper = np.maximum(calibrated_lower, calibrated_upper)

submission_df = pd.DataFrame({'id': X_test.index, 'pi_lower': calibrated_lower, 'pi_upper': calibrated_upper})
submission_df.to_csv('submission_final_ensemble_v2.csv', index=False)
print("\n'submission_final_ensemble_v2.csv' created successfully!")
display(submission_df.head())


--- Final Ensembling and Calibration ---
Final ENSEMBLE OOF Score (before calib): 332,965.69 | Coverage: 88.13%
Best calibration factor found: 1.059

'submission_final_ensemble_v2.csv' created successfully!


id       pi_lower      pi_upper
0  200000  823931.020766  1.123687e+06
1  200001  532291.577621  8.036857e+05
2  200002  435996.676950  7.284299e+05
3  200003  292412.598156  4.689401e+05
4  200004  410024.837004  7.064606e+05